# MCB 112 Problem Set 7


*deal with log of zeros!*

In [1]:
import numpy as np
import matplotlib.pyplot as plt     # optional
import scipy.stats as stats         # probably don't need
import scipy.special as special     # maybe, for logsumexp()
import seaborn as sns               # optional
import pandas as pd                 # optional

%matplotlib inline

In [2]:
def read_fasta(filename):
    '''
    Parses a FASTA file and returns only the sequence.

    Args:
        filename <str>: the name of the file.

    Returns:
        seq <str>: the sequences in the FASTA file.
    '''
    
    file = open(filename, 'r')
    # initiate list of sequences for multiple sequences in FASTA
    seqs = []
    seq = ""
    
    # loop through lines in file
    for line in file:
        # if the line is a descriptor line, don't add it to seq
        if line.startswith(">"):
            # check if it's the first sequence (in which case seq would be empty)
            if seq != "":
                # if it is not the first sequence, add the sequence to seqs
                seqs.append(seq.upper())
            # reset seq to store the next sequence
            seq = ""
        else:
            # if the line is not the delimiter line, strip() to get rid of the newline and then add it to the sequence
            seq += line.strip() 
    # add the last sequence (because this does not get triggered by another delimiter line)
    seqs.append(seq.upper())
    file.close()
    return seqs

In [3]:
aluminumjesus = read_fasta('AluminumJesus-upstream.fa')
hangryhippo = read_fasta('HangryHippo-upstream.fa')
t4 = read_fasta('T4-upstream.fa')

initialization

In [4]:
def initialize(seqs, W):
    '''
    Initializes a PWM and background matrix based on the input sequences

    Args:
        seqs <list(str)>: a list of sequences to initialize on
        W <int>: motif length

    Returns:
        init_bg <np.array(int)>: 4x1 array of background frequencies
        init_pwm <np.array(int)>: 4xW probability weight matrix of nucleotides in the motif
    '''

    init_pwm = np.zeros((4, W))
    init_bg = np.zeros((4,1))

    nt_to_index = {'A': 0, 'C': 1, 'G': 2, 'T': 3}

    # loop through sequences to collect expected counts
    for seq in seqs:
        L = len(seq)
        # sample a starting point lambda from a uniform distribution of all possible motif start positions
        lamb = np.random.randint(0,L - W + 1)
        # loop through columns i
        for i in range(len(seq)):
            # find nucleotide index (i.e. 'A' is 0)
            nt_index = nt_to_index[seq[i]]
            # if column i is not in the motif, add 1 count to background for whatever nucleotide it is
            if i < lamb or i >= lamb + W:
                init_bg[nt_index] += 1
            # if column i is in the motif, add 1 count to the pwm for whatever position of the motif and nucleotide it is
            else:
                init_pwm[nt_index,i - lamb] += 1

    # normalize by the total to turn counts into probabilities
    init_pwm = init_pwm / np.sum(init_pwm, axis=0)[np.newaxis,:]
    init_bg = init_bg / np.sum(init_bg)

    return init_bg, init_pwm


In [5]:
def posterior_dist(seq, W, init_bg, init_pwm):
    '''
    Finds probabilities of each possible starting lambda for a certain sequence, given a starting model theta

    Args:
        seq <str>: the sequence we're calculating the posterior on
        W <int>: motif length
        init_bg <np.array(float)>: 4x1 given background
        init_pwm <np.array(float)>: 4xW given probability weight matrix

    Returns:
        motif_probs <np.array(float)>: the probabilities of each possible starting lambda given the current model 
    '''
    nt_to_index = {'A': 0, 'C': 1, 'G': 2, 'T': 3}

    # initialize list to store probabilities of each lambda start position
    log_motif_probs = []

    log_bg = np.log(init_bg)

    # loop through all possible lambdas
    for lamb in range(len(seq) - W + 1):
        p_lamb = 0
        # loop through all columns i
        for i in range(len(seq)):
            nt_index = nt_to_index[seq[i]]

            # if column i is in motif, calculate probability of that lambda (and add 1e-10 as a pseudocount) given current model theta
            if lamb <= i < lamb + W:
                p_lamb += np.log(init_pwm[nt_index,i - lamb] + 1e-10)
            # if column i is not in motif, add probability that it is background given current model theta
            else:
                p_lamb += log_bg[nt_index]
        log_motif_probs.append(p_lamb)
    
    # find the bayesian denominator in log space by doing logsumexp over the list
    denom = special.logsumexp(log_motif_probs)

    # find final log probabilities by subtracting the log of the denominator
    log_motif_probs = log_motif_probs - denom

    # return exponentiated probabilities, not in log space
    return np.exp(log_motif_probs)

In [6]:
def expectation(seqs, W, init_bg, init_pwm):
    '''
    Calculates expected counts over all sequences given current model theta

    Args:
        seqs <list(str)>: sequences of interest
        W <int>: motif length
        init_bg <np.array(float)>: current model background
        init_pwm <np.array(float)>: current model pwm

    Returns:
        e_counts_bg <np.array(float)>: expected counts for background given current model
        e_counts_pwm <np.array(float)>: expected counts for motifs given current model
    '''
    nt_to_index = {'A': 0, 'C': 1, 'G': 2, 'T': 3}

    e_counts_bg = np.zeros((4,1))
    e_counts_pwm = np.zeros((4,W))

    # loop through sequences
    for i,seq in enumerate(seqs):
        L = len(seq)
        # find the list of posteriors for all lambdas on a particular sequence
        posterior = posterior_dist(seq, W, init_bg, init_pwm)

        # loop through possible lambdas
        for lamb in range(L - W + 1):
            # loop through columns k
            for k in range(L):
                nt = nt_to_index[seq[k]]
                # if column k in motif, add weighted count (the posterior for the lambda we're looping through) to new pwm
                if lamb <= k < lamb+W:
                    e_counts_pwm[nt,k - lamb] += posterior[lamb]
                # else column k not in motif, add weighted count to new background instead
                else:
                    e_counts_bg[nt] += posterior[lamb]

    return e_counts_bg, e_counts_pwm
            


In [7]:
def prob_given_counts(e_counts_bg, e_counts_pwm):
    '''
    Turn expected count matrices into probabilitiy matrices
    
    Args:
        e_counts_bg <np.array(float)>: expected counts of the background
        e_counts_pwm <np.array(float)>: expected counts of the PWM

    Returns:
        out_bg <np.array(float)>: probability matrix of background for each nucleotid
        out_pwm <np.array(float)>: probability weight matrix of motifs
    '''
    # add pseudocounts while summing over rows
    out_pwm = (e_counts_pwm + 1e-10) / (np.sum(e_counts_pwm, axis=0) + 1e-10)

    # normalize bg
    out_bg = (e_counts_bg + 1e-10) / np.sum(e_counts_bg)
    return out_bg, out_pwm

In [8]:
def relative_entropy(bg_mx, pwm_mx):
    '''
    Calculates relative entropy of a given PWM compared to background residue frequencies

    Args:
        bg_mx <np.array(float)>: given background frequencies
        pwm_mx <np.array(float)>: given PWM

    Returns:
        entropy (float): relative entropy
    '''
    entropy = 0
    # loop through possible motif locations k=1 to W
    for motif_loc in range(pwm_mx.shape[1]):
        # loop through nucleotides
        for a in range(4):
            # add entropy value to sum
            entropy += pwm_mx[a, motif_loc] * np.log2(pwm_mx[a, motif_loc] / bg_mx[a])

    return entropy
        

In [9]:
def motif_given_pwm(pwm):
    '''
    Calculates best motif given a PWM based on most likely probabilities in each column

    Args:
        pwm <np.array(float)>: given PWM

    Returns:
        motif <list(str)>: best motif
    '''
    motif = []
    nts = ['A', 'C', 'G', 'T']

    # loop through motif columns
    for motif_loc in range(pwm.shape[1]):
        # find the most probable nucleotide in each column and add it to our motif
        motif.append(nts[np.argmax(pwm[:,motif_loc])])

    return motif

In [10]:
def em_alg(seqs, W, iterations):
    '''
    Run expectation-maximization algorithm and return theta and entropy and the best motif

    Args:
        seqs <list(str)>: sequences of interest
        W <int>: motif length
        iterations <int>: the number of iterations for convergence criteria

    Returns:
        bg_mx <np.array(float)>: final model background
        pwm_mx <np.array(float)>: final model PWM
        entropy_motif <float>: relative entropy of PWM and background
        motif <list(str)>: best motif given PWM
    '''
    # start by initializing a theta based on the given sequences
    bg_mx, pwm_mx = initialize(seqs, W)

    # convergence criteria here is just a large enough number of iterations
    for i in range(iterations):
        # expectation step: given model, infer posterior
        bg_mx_unnorm, pwm_mx_unnorm = expectation(seqs, W, bg_mx, pwm_mx)

        # maximization step: given posterios, infer new model
        bg_mx, pwm_mx = prob_given_counts(bg_mx_unnorm, pwm_mx_unnorm)

    # find entropy and best motif
    entropy_motif = relative_entropy(bg_mx, pwm_mx)
    motif = motif_given_pwm(pwm_mx)
    return bg_mx, pwm_mx, entropy_motif, motif

In [11]:
def optimize(runs, seqs, W, iterations):
    '''
    Run EM multiple times since EM is a local optimizer and calculate the best entropy and best motif

    Args:
        runs <int>: number of runs/initializations to do
        seqs <list(str)>: sequences of interest
        W <int>: motif length
        iterations <int>: the number of iterations for convergence criteria

    Returns:
        bg <np.array(float)>: final model background
        pwm <np.array(float)>: final model PWM
        best_entropy <float>: relative entropy of PWM and background
        best_motif <list(str)>: best motif given PWM
    '''
    # compare all entropy values to a starting point of negative infinity
    best_entropy = - np.inf

    # run the algorithm given number of times
    for i in range(runs):

        # expectation-maximization
        bg, pwm, entropy, motif = em_alg(seqs, W, iterations)

        # check if output entropy is better than the best one we have
        if entropy > best_entropy:
            # if yes, store it as the best entropy and motif
            best_entropy = entropy
            best_motif = motif

    return bg, pwm, best_entropy, best_motif


### Part 2: Synthetic Positive Control

In [12]:
def gen_pos_control(pwm, bg, W, N, L):
    '''
    Generate list of N sequences of length L with an embedded motif according to given model theta

    Args:
        pwm <np.array(float)>: given model PWM
        bg <np.array(float)>: given model background
        W <int>: motif length
        N <int>: number of sequences to generate
        L <int>: length of each sequence

    Returns:
        seqs <list(str)>: list of positive control sequences
    '''
    seqs = []

    # generate N sequences
    for n in range(N):
        seq = []
        # randomly choose a starting point for the motif in each sequence
        rand_lambda = np.random.randint(L)
        for l in range(L):
            # if the column is in the motif
            if rand_lambda <= l < rand_lambda + W:
                # find nt based on pwm
                seq.append(np.random.choice(['A','C','G','T'], p = pwm[:,l - rand_lambda]))
            # else the column is not in the motif
            else:
                # find nt based on background
                seq.append(np.random.choice(['A','C','G','T'], p = bg))
        seqs.append("".join(seq))

    return seqs


I embedded motif 'ACGT' in the positive control sequences.

In [13]:
pos_ctrl_pwm = np.array(([.99,.003,.003,.003],
                        [0.003,0.99,0.003,0.003],
                        [0.003,0.003,0.99,0.004],
                        [0.004,0.004,0.004,0.99]))

pos_ctrl_bg = np.array([.25,.25,.25,.25])

pos_ctrl_seqs = gen_pos_control(pos_ctrl_pwm, pos_ctrl_bg, 4, 200, 50)

In [14]:
pos_bg, pos_pwm, pos_entropy, pos_motif = optimize(5, pos_ctrl_seqs, 4, iterations=100)

/var/folders/9c/jnjk1w9d5qs92p8vmp8nl2740000gn/T/ipykernel_25527/850263856.py:16: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  e_counts_pwm[nt,k - lamb] += posterior[lamb]


In [15]:
print(pos_entropy, pos_motif)

[7.34116705] ['A', 'C', 'G', 'T']


We see that our algorithm was able to find this motif, yay!

### Part 3: Negative Control

In [16]:
def gen_neg_control(N, L):
    '''
    Generate N completely random sequences of length L

    Args:
        N <int>: number of sequences
        L <int>: length of sequences

    Returns:
        seqs <list(str)>: list of negative control seqs
    '''
    seqs = []

    # generate N random sequences
    for i in range(N):
        seq = np.random.choice(['A','C','G','T'], size=L)
        seqs.append("".join(seq))

    return seqs

In [17]:
neg_ctrl_seqs = gen_neg_control(200, 50)

In [18]:
neg_bg, neg_pwm, neg_entropy, neg_motif = optimize(5, neg_ctrl_seqs, 4, iterations=100)

/var/folders/9c/jnjk1w9d5qs92p8vmp8nl2740000gn/T/ipykernel_25527/850263856.py:16: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  e_counts_pwm[nt,k - lamb] += posterior[lamb]


In [19]:
print(neg_entropy, neg_motif)

[1.87903975] ['A', 'C', 'A', 'G']


We see that the relative entropy value for the negative control sequences is much lower than the relative entropy value fo the positive control sequences, because there shouldn't be any convincing motif in these sequences. We didn't embed anything!

### Part 4: ribosome binding sites!

What is the best ribosome binding site motif of the AluminumJesus phage?

In [20]:
motif_lengths = [4,5,6,7,8]
for motif_length in motif_lengths:
    aljesus_bg, aljesus_pwm, aljesus_entropy, aljesus_motif = optimize(5, aluminumjesus, motif_length, iterations=100)
    print("For motifs of length ", motif_length, ", the best motif is ", aljesus_motif, ", with relative entropy score of ", aljesus_entropy)


/var/folders/9c/jnjk1w9d5qs92p8vmp8nl2740000gn/T/ipykernel_25527/850263856.py:16: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  e_counts_pwm[nt,k - lamb] += posterior[lamb]


For motifs of length  4 , the best motif is  ['G', 'G', 'A', 'G'] , with relative entropy score of  [4.28515507]
For motifs of length  5 , the best motif is  ['G', 'G', 'A', 'G', 'G'] , with relative entropy score of  [4.65636345]
For motifs of length  6 , the best motif is  ['G', 'G', 'A', 'G', 'G', 'A'] , with relative entropy score of  [4.93949542]
For motifs of length  7 , the best motif is  ['G', 'G', 'A', 'G', 'G', 'A', 'G'] , with relative entropy score of  [5.20019641]
For motifs of length  8 , the best motif is  ['G', 'G', 'A', 'G', 'G', 'A', 'G', 'A'] , with relative entropy score of  [5.5572531]


What is the best ribosome binding site motif of the HangryHippo phage?

In [24]:
motif_lengths = [4,5,6,7,8]
for motif_length in motif_lengths:
    hh_bg, hh_pwm, hh_entropy, hh_motif = optimize(5, hangryhippo, motif_length, iterations=100)
    print("For motifs of length ", motif_length, ", the best motif is ", hh_motif, ", with relative entropy score of ", hh_entropy)

/var/folders/9c/jnjk1w9d5qs92p8vmp8nl2740000gn/T/ipykernel_25527/850263856.py:16: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  e_counts_pwm[nt,k - lamb] += posterior[lamb]


For motifs of length  4 , the best motif is  ['G', 'G', 'A', 'G'] , with relative entropy score of  [4.32642428]
For motifs of length  5 , the best motif is  ['G', 'G', 'A', 'G', 'G'] , with relative entropy score of  [4.62676519]
For motifs of length  6 , the best motif is  ['A', 'G', 'G', 'A', 'G', 'G'] , with relative entropy score of  [4.76894581]
For motifs of length  7 , the best motif is  ['A', 'G', 'G', 'A', 'G', 'G', 'A'] , with relative entropy score of  [4.80068465]
For motifs of length  8 , the best motif is  ['A', 'G', 'G', 'A', 'G', 'G', 'A', 'A'] , with relative entropy score of  [4.89711089]


What is the best ribosome binding site motif of the T4 phage?

In [25]:
motif_lengths = [4,5,6,7,8]
for motif_length in motif_lengths:
    t4_bg, t4_pwm, t4_entropy, t4_motif = optimize(5, t4, motif_length, iterations=100)
    print("For motifs of length ", motif_length, ", the best motif is ", t4_motif, ", with relative entropy score of ", t4_entropy)


/var/folders/9c/jnjk1w9d5qs92p8vmp8nl2740000gn/T/ipykernel_25527/850263856.py:16: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  e_counts_pwm[nt,k - lamb] += posterior[lamb]


For motifs of length  4 , the best motif is  ['G', 'A', 'G', 'G'] , with relative entropy score of  [5.38908574]
For motifs of length  5 , the best motif is  ['G', 'A', 'G', 'G', 'A'] , with relative entropy score of  [5.60628634]
For motifs of length  6 , the best motif is  ['G', 'A', 'G', 'G', 'A', 'A'] , with relative entropy score of  [5.84615741]
For motifs of length  7 , the best motif is  ['G', 'A', 'G', 'G', 'A', 'A', 'A'] , with relative entropy score of  [5.8436511]
For motifs of length  8 , the best motif is  ['G', 'A', 'G', 'G', 'A', 'A', 'A', 'A'] , with relative entropy score of  [5.8727488]


For the Aluminum Jesus phage, I think the best motif is GGAGG. For the Hangry Hippo phage, I think the best motif is also GGAGG. For the T4 phage, I think the best motif is GAGGA.

#### Watermark!

In [26]:
import watermark
%load_ext watermark 
%watermark -v -m -p numpy,matplotlib,scipy,seaborn,pandas

Python implementation: CPython
Python version       : 3.12.4
IPython version      : 8.25.0

numpy     : 1.26.4
matplotlib: 3.9.2
scipy     : 1.13.1
seaborn   : 0.13.2
pandas    : 2.2.2

Compiler    : Clang 14.0.6 
OS          : Darwin
Release     : 23.4.0
Machine     : arm64
Processor   : arm
CPU cores   : 12
Architecture: 64bit

